In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import time
import matplotlib.animation as ami
import os
import imageio.v2 as imageio
np.seterr(over="ignore")
metadata = dict(title='power fractal', artist='jason',comment=':)')
writer = ami.FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)

In [ ]:
# def power_diverge(z, n_max=100):
#     z_o = z**z
#     for i in range(n_max):
#         z_o = z**z_o
#         if abs(z_o) > 1e11:
#             return n_max
#     return 0

# def power_fractal(param, param_x, param_y, N=1001, n=100):
#     A = np.zeros((N, N), dtype=int)
#     x = np.linspace(param_x-param/2, param_x+param/2, N)
#     y = np.linspace(param_y-param/2, param_y+param/2, N)
#     X, Y = np.meshgrid(x, y)
#     Z = X + 1j * Y
#     for i in range(N):
#         for j in range(N):
#             z_n = Z[i, j]
#             A[i, j] = power_diverge(z_n, n_max=n)
#     plt.imshow(A, extent=(param_x-param/2, param_x+param/2, param_y-param/2, param_y+param/2))
#     plt.title('Power Tower Fractal')
#     plt.xlabel('Real(C)')
#     plt.ylabel('Imaginary(C)')
#     plt.show()

# Optimized power fractal (vectorized) (4x faster than before)
def power_fractal(bounds, N=1001, n=100):
    x_min, x_max, y_min, y_max = bounds
    A = np.zeros((N, N), dtype=np.complex128)
    x = np.linspace(x_min, x_max, N)
    y = np.linspace(y_min, y_max, N)
    X, Y = np.meshgrid(x, y)
    Z = X + 1j * Y
    num_iter = np.full(Z.shape, n)
    for i in range(n):
        mask = (num_iter == n)
        A[mask] = Z[mask] ** A[mask]
        num_iter[mask & (np.abs(A) > (1e11))] = i + 1
    num_iter = ~num_iter #lazy fix lol
    return num_iter

# p = "frames" from animation function call
def animate_fractal(p, N=1001):
    ax.clear()  
    ax.set_xticks([], []) 
    ax.set_yticks([], []) 
    #box = bounds(0.1, (0.91, -2.46))
    box = bounds(0.0000000001, (0.91+0.0001-0.0000001, -2.46-0.0001))
    power_set = power_fractal(box, N=N, n=p)
    img = ax.imshow(power_set, extent=box, cmap="inferno")
    return [img]


def animate_zoom(writer, max_iter=10): 
    init_box = bounds(20, (0, 0))
    #zoom_point = (-0.188-0.00000020927,0.2361-0.000000209261)
    zoom_point = (0.91+0.0001-0.0000001, -2.46-0.0001)

    fig = plt.figure(figsize=(10, 10)) 
    ax = plt.axes() 
    ax.set_axis_off()
    #need a for loop for zoom which is an issue (use nested function instead with nonlocal)
    def update_zoom(p):
        nonlocal init_box
        img = power_fractal(init_box, N=1001, n=200)
        im = ax.imshow(img, extent=init_box, cmap="inferno")
        init_box = zoom(zoom_point, init_box)
        return [im]

    ani = ami.FuncAnimation(fig, update_zoom, frames=max_iter, repeat=False)
    ani.save("zoom.mp4", writer=writer)
    
#returns boundary of range (interval) centered at point
def bounds(interval, point):
    x, y = point
    return x-interval/2, x+interval/2, y-interval/2, y+interval/2

#point = zoom point
#box = boundary box
#factor = zoom factor
def zoom(point, box, factor=1.1):
    factor = 2*factor
    x, y = point
    x_min, x_max, y_min, y_max = box
    width = (x_max-x_min)/factor
    height = (y_max-y_min)/factor
    return x-width, x+width, y-height, y+height

In [ ]:
# Testing runtime
#start_time = time.time()
box = bounds(20, (0, 0))
img = power_fractal(box)
plt.imshow(img, extent=box,cmap="inferno")
#ax = plt.axes() 
#ax.set_axis_off()
#plt.savefig("fractal.png")
plt.show()
#print("--- %s seconds ---" % (time.time() - start_time))

In [ ]:
#Testing
box = bounds(9, (0, 0))
img = power_fractal(box)
plt.imshow(img, extent=box, cmap="inferno")
plt.show()

In [ ]:
#Testing
#box = bounds(0.000000000002, (-0.188-0.00000020927,0.2361-0.000000209261))
box = bounds(0.0000000001, (0.91+0.0001-0.0000001, -2.46-0.0001))
img = power_fractal(box, n=300)
plt.imshow(img, extent=box, cmap="inferno")
plt.show()

In [ ]:
#Testing
box = bounds(0.8, (-0.25, 0))
img = power_fractal(box)
plt.imshow(img, extent=box, cmap="inferno")
plt.show()

In [ ]:
#Testing
box = bounds(0.1, (0.91, -2.46))
img = power_fractal(box)
plt.imshow(img, extent=box, cmap="inferno")
plt.show()

In [ ]:
#Testing animation (animates the formation of fractal (control "n"))
fig = plt.figure(figsize=(10, 10)) 
ax = plt.axes() 
anim = ami.FuncAnimation(fig, animate_fractal, frames=np.arange(200), interval=50, blit=True)
anim.save('fractal_basic.mp4', writer=writer)

In [ ]:
#Test zoom
init_box = bounds(20, (0, 0))
#zoom_point = (-0.188-0.00000020927,0.2361-0.000000209261)
zoom_point = (0.91+0.0001-0.0000001, -2.46-0.0001)
box = zoom(zoom_point, init_box)
for i in range(20):
    img = power_fractal(box, N=1001, n=200)
    plt.imshow(img, extent=box, cmap="inferno")
    plt.show()
    box = zoom(zoom_point, box, factor=2)

In [ ]:
animate_zoom(writer, max_iter=150)